# # 1
# 영문: 토큰화, 모든 단어를 기본형으로 변환, 유의미 품사 추출
# 한글: 형태소 분석, 유의미 형태소 추출
# 각 단어별로 장소 임베딩
# # 2
# word2vec으로 모든 단어를 임베딩한 후,
# k-means clustering으로 군집화하여 군집별로 장소 임베딩

In [1]:
import numpy as np
import pandas as pd
import re
import os
import platform
import multiprocessing as mp
from multiprocessing import Pool
import sys
import time
import pickle
import konlpy
from konlpy.tag import Mecab

list_csv = ['data/kor/attraction_review_tag.csv',
            'data/kor/hotel_review_tag.csv',
            'data/kor/restaurant_review_tag.csv',
            'data/eng/eng_attraction_review_tag.csv',
            'data/eng/eng_hotel_review_tag.csv',
            'data/eng/eng_restaurant_review_tag.csv']
list_corpus = ['corpus/attraction_tag.list',
               'corpus/hotel_tag.list',
               'corpus/restaurant_tag.list',
               'corpus/eng_attraction_tag.list',
               'corpus/eng_hotel_tag.list',
               'corpus/eng_restaurant_tag.list']
try:
    os.stat('corpus')
except:
    os.mkdir('corpus')
try:
    os.stat('corpus/token')
except:
    os.mkdir('corpus/token')

In [82]:
db_csv = ['data/attraction_db.csv',
            'data/hotel_db.csv',
            'data/restaurant_db.csv']
df_db = pd.read_csv(db_csv[0])
df_db = df_db.drop(columns=['class', 'score', 'name_eng', 'latitude', 'longitude'])
df = pd.read_csv(list_csv[0])
df = df.drop(columns=['review'])
count = df['placeId'].value_counts()
df_cnt = count.to_frame(name='count')
df_cnt.reset_index(level=0, inplace=True)
df_cnt.columns = ['placeId', 'count']

In [78]:
pd.options.display.max_rows = 1000

In [83]:
df_cnt = df_cnt.merge(df_db, how='left')
df_cnt

placeId  count                 name_kor
0     2194168    789                    서울메트로
1      324888    599                      경복궁
2      324891    567                     롯데월드
3      553546    552                 명동 쇼핑 거리
4     1169465    538                  N 서울 타워
5     1046419    435                      청계천
6      592506    428                      인사동
7     1379963    342                  북촌 한옥마을
8      554537    305                한국 전쟁 기념관
9     1552278    299                     광장시장
10     325043    261                  국립중앙박물관
11    1958940    250                   홍대앞 거리
12    6671988    240              동대문 디자인 플라자
13     554582    222                    남산 공원
14     592658    197                   올림픽 공원
15     320359    190                      창덕궁
16    1604009    173                     가로수길
17     554528    164                 북한산 국립공원
18     592486    163                      봉은사
19    1957627    161                   여의도 공원
20     609340    159                    명동 성당
21    4798715    158                 여의도 한강공원
22     592495    156                코엑스 아쿠아리움
23    1643534    153                  한가람 미술관
24    6656879    153                     삼청동길
25     324907    135                    남대문시장
26     590748    126                      광화문
27    8842556    125                 롯데월드타워&몰
28     592490    124               서울 어린이 대공원
29    6847900    123                   광화문 광장
30     324887    118                      덕수궁
31    8737878    118                   그레뱅뮤지엄
32    4798711    118                      서울숲
33    1862191    100                  이화여자대학교
34    2008729     94                잠실 야구 경기장
35     598499     89                 삼성미술관 리움
36    4094861     87                     하늘공원
37    1554603     84                      창경궁
38    1551271     83                남산골 한옥 마을
39    8693245     82               3D블랙아트 박물관
40    1440196     80              서대문 형무소 역사관
41    4084344     77                    서울 시청
42     554303     76                스타필드 코엑스몰
43    4095685     73                     낙산공원
44    1766551     73                      쌈지길
45    1235392     71                      조계사
46    1831099     70                    국립국악원
47    2571660     68                      이태원
48    1579821     65                  세종대왕 동상
49    3822061     62                    IFC 몰
50    2203080     62               트릭아이뮤지엄 서울
51     554634     62                       종묘
52    1842046     60                노량진 수산 시장
53     554551     60                     63시티
54    1990451     60                    타임스퀘어
55    3322253     56                      KTX
56     324890     53                국립 민속 박물관
57    1960138     53                문화역서울 284
58    2094166     52                서울 역사 박물관
59     553213     52                   서울 대학로
60     561808     48  서울 월드컵 경기장 (상암 월드컵 경기장)
61    3871936     46              국립현대미술관 서울관
62    2476788     45                   디큐브 시티
63     553246     44                       신촌
64     592484     44               충무공 이순신 동상
65    1962594     41                 롯데백화점 본점
66    3600495     40                  남산 케이블카
67    3901448     39              경희대학교 서울캠퍼스
68     554533     38               동대문 (흥인지문)
69    6352852     35                  메세나폴리스몰
70    3694519     35                  이화 벽화마을
71    2011401     34               신세계 백화점 본점
72    1675961     33                   선릉과 정릉
73    6570666     32                  이대 패션거리
74    1809989     31                서울 시립 미술관
75    2341905     31             동대문 역사 문화 공원
76    4084386     30                북악산 서울 성곽
77    2293574     29                    서울 광장
78    3568803     29                     반포대교
79    1418675     29                   코엑스 센터
80    3694539     28                   대림 미술관
81    4095502     28                    아이파크몰
82    3808315     27                      숭례문
83    1758805     25                      청와대
84    2173769     25                      세빛섬
85    8798065     24               롯데월드 아쿠아리움
86  

In [28]:
# 순서유지 집합리스트화
def orderset(seq):
    seen = set()
    seen_add = seen.add
    return [x for x in seq if not (x in seen or seen_add(x))]
# corpus 생성함수
def mkcorpus(ws):
    subcorpus = []
    for word in ws :
        places = []
        for i in range(len(df_morpheme)):
            if word in df_morpheme['tags'][i]:
                #태그문장 내 동일 장소 중복 방지
                #if not df_morpheme['placeId'][i] in places:
                    places.append(df_morpheme['placeId'][i])
        subcorpus.append(places)
    return subcorpus 

# 한글

In [8]:
if platform.system() == 'Linux':
    mecab = Mecab()
elif platform.system() == 'Windows':
    mecab = Mecab(dicpath="C:\\mecab\\mecab-ko-dic")

In [5]:
for csv in range(3):
    df = pd.read_csv(list_csv[csv])
    # filter charset exception
    df['review'] = df['review'].apply(lambda x: re.sub(r'[^ 가-힣0-9.!?\n]',' ',x))
    # make sentence list
    array = df['review'].tolist()
    # 한글형태소 분리
    list_pos = [mecab.pos(sentence) for sentence in array]
    # 형태소 리스트화
    morpheme = [mecab.morphs(sentence) for sentence in array]

    # 의미를 가지는 형태소만 추출
    pattern = re.compile('MM|NNG|VA[+].*|VV[+].*|XR')
    df_morpheme = pd.DataFrame(columns = ['placeId','tags'], dtype = 'int64')
    taglist = []
    for i in range(len(list_pos)):
        pairs = np.array(list_pos[i])
        tags = np.array(morpheme[i])
        npbool = []
        for pair in pairs:
            npbool.append(re.fullmatch(pattern,pair[1])!=None)
        tags = tags[npbool]
        taglist.append(tags.tolist())
    df_morpheme['tags'] = taglist
    df_morpheme['placeId'] = df['placeId'].astype('int64')

    wordlist = []
    for l in df_morpheme['tags']:
        wordlist += l
    wordset = orderset(wordlist)
    print('In ',list_csv[csv])
    print('단어전체', len(wordlist))
    print('단어집합', len(wordset))
    # 병렬처리를 위한 데이터 분할 
    core_count = mp.cpu_count()
    wordsubset = np.array_split(wordset, core_count)
    # 멀티프로세스 연산
    if __name__ == '__main__':
        start = time.time()

        pool = Pool(core_count)
        subcorpora = pool.map(mkcorpus, wordsubset)
        pool.close()
        pool.join()
        
        corpus = []
        for i in subcorpora:
            corpus += i
        print('Elapsed time(corpus): ', str(time.time() - start), ' secs')
        # save
        # 개수가 단어집합과 동일해야함
        print('Length of corpus: ', len(corpus))
        # save
        with open(list_corpus[csv],'wb') as f:
            pickle.dump(corpus, f)

전체 246208
집합 13226


# 영문

In [ ]:
# 현재는 의미있는 품사만 고른후 그대로 corpus 구성
# stem, lemmatize후 구성하도록 수정하고 성능 비교해보기

In [2]:
import nltk
from nltk.stem import PorterStemmer
from nltk.stem import WordNetLemmatizer
nltk.data.path.append('F:\\소공전프로젝트\\sofcon\\recomm\\nltk_data')
list_tokens = ['corpus/token/eng_attraction.token',
               'corpus/token/eng_hotel.token',
               'corpus/token/eng_restaurant.token']

In [7]:
for csv in range(3,6):
    df = pd.read_csv(list_csv[csv])
    # filter charset exception
    df['review'] = df['review'].apply(lambda x: re.sub(r'[^ a-zA-Z0-9.!?\'\n]',' ',x))
    # make sentence list
    array = df['review'].tolist()
    # Load if token file exists, tokenize if not.
    try:
        os.stat(list_tokens[csv-3])
        with open(list_tokens[csv-3],'rb') as f:
            pickle.dump(tokens, f)
        print('Token loaded from ', list_tokens[csv-3])
    except:
        start = time.time()
        tokens = [nltk.word_tokenize(sentence) for sentence in array]
        print('Elapsed time(tokenize): ', str(time.time() - start), ' secs')
    
    start = time.time()
    pos_tagged = [nltk.pos_tag(sentence) for sentence in tokens]
    print('Elapsed time(pos-tag): ', str(time.time() - start), ' secs')
    tagpat = r'(JJ[RS]*)|(NN[P]*[S]*)|(RB[RS]*)|(VB[DGNPZ]*)'

    start = time.time()
    sub_pos_tagged = []
    for sentence in pos_tagged:
        subsentence = [word[0] for word in sentence if not re.fullmatch(tagpat, word[1]) == None]
        sub_pos_tagged.append(subsentence)
    print('Elapsed time(filter): ', str(time.time() - start), ' secs')

    df_morpheme = pd.DataFrame(columns = ['placeId', 'tags'], dtype='int64')
    df_morpheme['placeId'] = df['placeId'].astype('int64')
    df_morpheme['tags'] = sub_pos_tagged

    wordlist = []
    for l in df_morpheme['tags']:
        wordlist += l
    wordset = orderset(wordlist)
    print('In ',list_csv[csv])
    print('단어전체', len(wordlist))
    print('단어집합', len(wordset))
    # 병렬처리를 위한 데이터 분할 
    core_count = mp.cpu_count()
    wordsubset = np.array_split(wordset, core_count)
    # 멀티프로세스 연산
    if __name__ == '__main__':
        start = time.time()
        pool = Pool(core_count)
        subcorpora = pool.map(mkcorpus, wordsubset)
        pool.close()
        pool.join()
        corpus = []
        for i in subcorpora:
            corpus += i
        print('Elapsed time(corpus): ', str(time.time() - start), ' secs')
        # save
        # 개수가 단어집합과 동일해야함
        print('Length of corpus: ', len(corpus))
        with open(list_corpus[csv],'wb') as f:
            pickle.dump(corpus, f)

Elapsed time(tokenize):  113.04303431510925  secs
Elapsed time(filter):  2.126061201095581  secs
In  data/eng/eng_hotel_review_tag.csv
단어전체 1339512
단어집합 34074


"\n    # 멀티프로세스 연산\n    if __name__ == '__main__':\n        start = time.time()\n\n        corpus = []\n        pool = Pool(core_count)\n        pool.map(mkcorpus, wordsubset)\n        pool.close()\n        pool.join()\n        print('Elapsed time(corpus): ', str(time.time() - start), ' secs')\n        # save\n        with open(list_corpus[csv],'wb') as f:\n            pickle.dump(corpus, f)"

In [90]:
import pickle
with open('corpus/token/eng_attraction.token', 'rb') as f:
    tokens = pickle.load(f)
pos_tagged = [nltk.pos_tag(sentence) for sentence in tokens]
tagpat = r'(JJ[RS]*)|(NN[P]*[S]*)|(RB[RS]*)|(VB[DGNPZ]*)'

sub_pos_tagged = []
for sentence in pos_tagged:
    subsentence = [word for word in sentence if not re.fullmatch(tagpat, word[1]) == None]
    sub_pos_tagged.append(subsentence)

In [89]:
sub_pos_tagged

[['secret',
  'garden',
  'changdeokgung',
  'have',
  'be',
  'changdeokgung',
  'secret',
  'garden',
  'twice',
  'now',
  'best',
  'time',
  'go',
  'be',
  'springtim',
  'flower',
  'be',
  'full',
  'bloom',
  'garden',
  'be',
  'aliv',
  'bird',
  'song',
  'autumn',
  'be',
  'also',
  'amaz',
  'fall',
  'foliag',
  'look',
  'splendid',
  'complement',
  'palac',
  'build',
  'be',
  'grand',
  'palac',
  'seoul',
  'be',
  'conveni',
  'locat',
  'nearbi',
  'other',
  'popular',
  'tourist',
  'attract',
  'be',
  'separ',
  'entranc',
  'fee',
  'changdeokgung',
  'palac',
  'secret',
  'garden',
  'boast',
  'pavilion',
  'lili',
  'pond',
  'stream',
  'a',
  'well',
  'lusciou',
  'veget',
  'onli',
  'enter',
  'secret',
  'garden',
  'part',
  'organi',
  'tour',
  'tour',
  'be',
  'korean',
  'english',
  'japan',
  'chine',
  'more',
  'detail',
  'inform',
  'mani',
  'photograph',
  'plea',
  'have',
  'look',
  'blog',
  'post'],
 ['secret',
  'garden',
  'be

In [ ]:
from nltk.corpus import wordnet
def posclass(tag):
    if tag in ['JJ', 'JJR', 'JJS']
        return wordnet.ADJ 
    elif tag in ['NN', 'NNP', 'NNS', 'NNPS']
        return wordnet.NOUN
    elif tag in ['RB', 'RBR', 'RBS']
        return wordnet.ADV
    elif tag in ['VB', 'VBD', 'VBG', 'VBN', 'VBP', 'VBZ']
        return wordnet.VERB

In [80]:
st = PorterStemmer()
lm = WordNetLemmatizer()
start = time.time()
for sentence in sub_pos_tagged:
    for word in range(len(sentence)):
        sentence[word] = st.stem(sentence[word])
        sentence[word] = lm.lemmatize(sentence[word], pos='v')
print('Elapsed time(lemmatize): ', str(time.time() - start), ' secs')

Elapsed time(lemmatize):  44.309072732925415  secs


In [72]:
sub_pos_tagged

[['secret',
  'garden',
  'changdeokgung',
  'have',
  'been',
  'changdeokgung',
  'secret',
  'garden',
  'twice',
  'now',
  'best',
  'time',
  'go',
  'be',
  'springtim',
  'flower',
  'are',
  'full',
  'bloom',
  'garden',
  'is',
  'aliv',
  'bird',
  'song',
  'autumn',
  'is',
  'also',
  'amaz',
  'fall',
  'foliag',
  'look',
  'splendid',
  'complement',
  'palac',
  'build',
  'is',
  'grand',
  'palac',
  'seoul',
  'is',
  'conveni',
  'locat',
  'nearbi',
  'other',
  'popular',
  'tourist',
  'attract',
  'is',
  'separ',
  'entranc',
  'fee',
  'changdeokgung',
  'palac',
  'secret',
  'garden',
  'boast',
  'pavilion',
  'lili',
  'pond',
  'stream',
  'a',
  'well',
  'lusciou',
  'veget',
  'onli',
  'enter',
  'secret',
  'garden',
  'part',
  'organis',
  'tour',
  'tour',
  'are',
  'korean',
  'english',
  'japanes',
  'chine',
  'more',
  'detail',
  'inform',
  'mani',
  'photograph',
  'plea',
  'have',
  'look',
  'blog',
  'post'],
 ['secret',
  'garden'

In [5]:
with open(list_corpus[0],'rb') as f:
    l = pickle.load(f)

In [6]:
l

[['320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '320359',
  '324887',
  '324887',
  '324887',
  '324887',
  '324887',
  '324887',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '324888',
  '3